In [1]:
%matplotlib qt
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FFMpegWriter

In [2]:
#initialize pinhole camera and screen
camera = np.array([0, 0, 1])

#moving camera
# y_range = np.linspace(-0.9, 0.9, 50)
# cameras = []
# for y in y_range:
#     cameras.append(np.array([y, y, 3]))


#change resolution as needed
h = 200
w = 300

screen = (-1, h/w, 1, -h/w) # ratio boundaries of screen

In [3]:
#helper functions
def norm(vec):
    return vec/np.linalg.norm(vec)

class Sphere():
    def __init__(self, x, y, z, r, ambient, diffuse, specular, shine, reflect):
        self.x = x
        self.y = y
        self.z = z
        self.r = r
        self.ambient = ambient
        self.diffuse = diffuse
        self.specular = specular
        self.shine = shine
        self.reflect = reflect
        
    def get_center(self):
        return np.array([self.x, self.y, self.z])
    
class Light():
    def __init__(self, x, y, z, ambient, diffuse, specular):
        self.x = x
        self.y = y
        self.z = z
        self.ambient = ambient
        self.diffuse = diffuse
        self.specular = specular 
        
    def get_center(self):
        return np.array([self.x, self.y, self.z])

#source: https://github.com/ProgrammierPatrick/sightpy-lab/blob/master/sightpy/geometry/sphere.py
def intersect_object(obj, origin, ray): #only works with spheres for now
#     sphere_center = get_center(obj)
#     sphere_radius = get_radius_sphere(obj)
    center = obj.get_center()
    radius = obj.r
    shift = origin - center
    
    #get nearest point when both intersections are positive
    b = 2*np.dot(shift, ray)
    c = (np.linalg.norm(shift)**2) - (radius**2)
    d = (b**2) - 4*c
    
    #check if d > 0 to get sqrt
    if d > 0:
        intersect1 = (-b + np.sqrt(d)) / 2
        intersect2 = (-b - np.sqrt(d)) / 2
        if (intersect1 > 0) and (intersect2 > 0):
            return min(intersect1, intersect2)
    
    #else no intersection
    return None
    
def find_nearest_object(objects, origin, ray):
    distances = []
    for obj in objects:
        center = obj.get_center()
        radius = obj.r
        curr_dist = intersect_object(obj, origin, ray)
        distances.append(curr_dist)
    
    nearest_object = None
    min_dist = np.inf
    for d in range(len(distances)):
        if distances[d] is not None:
            if distances[d] < min_dist:
                min_dist = distances[d]
                nearest_object = objects[d]
    return nearest_object, min_dist
    
def reflected_ray(ray, axis):
    return ray - 2*axis*np.dot(ray, axis)

In [4]:
#create objects: 
objects = []

#move object
move_range = np.linspace(-0.5, 0.5, 25)
move_range_back = np.linspace(0.5, -0.5, 25)
for val in move_range:
    objects.append([Sphere(val, 0.5, -1, 0.4, np.array([0.1, 0, 0.1]), np.array([0.7, 0, 0.6]), np.array([1, 1, 1]), 100, 0.5), Sphere(0, -9000, 0, 8999.3, np.array([0.1, 0.1, 0.1]), np.array([0.5, 0.5, 0.5]), np.array([1, 1, 1]), 100, 0.5)])
for val in move_range_back:
    objects.append([Sphere(0.5, val, -1, 0.4, np.array([0.1, 0, 0.1]), np.array([0.7, 0, 0.6]), np.array([1, 1, 1]), 100, 0.5), Sphere(0, -9000, 0, 8999.3, np.array([0.1, 0.1, 0.1]), np.array([0.5, 0.5, 0.5]), np.array([1, 1, 1]), 100, 0.5)])
for val in move_range_back:
    objects.append([Sphere(val, -0.5, -1, 0.4, np.array([0.1, 0, 0.1]), np.array([0.7, 0, 0.6]), np.array([1, 1, 1]), 100, 0.5), Sphere(0, -9000, 0, 8999.3, np.array([0.1, 0.1, 0.1]), np.array([0.5, 0.5, 0.5]), np.array([1, 1, 1]), 100, 0.5)])
for val in move_range:
    objects.append([Sphere(-0.5, val, -1, 0.4, np.array([0.1, 0, 0.1]), np.array([0.7, 0, 0.6]), np.array([1, 1, 1]), 100, 0.5), Sphere(0, -9000, 0, 8999.3, np.array([0.1, 0.1, 0.1]), np.array([0.5, 0.5, 0.5]), np.array([1, 1, 1]), 100, 0.5)])

#changing rgb values
# rgb_range = np.linspace(0, 1, 25)
# rgb_range_back = np.linspace(1, 0, 25)
# for val in rgb_range: #r
#     objects.append([Sphere(0, 0, -1, 0.8, np.array([0.1, 0, 0]), np.array([val, 0, 0]), np.array([1, 1, 1]), 100, 0.5), Sphere(0, -9000, 0, 8999.3, np.array([0.1, 0.1, 0.1]), np.array([0.5, 0.5, 0.5]), np.array([1, 1, 1]), 100, 0.5)])
# for val in rgb_range_back:
#     objects.append([Sphere(0, 0, -1, 0.8, np.array([0.1, 0, 0]), np.array([val, 0, 0]), np.array([1, 1, 1]), 100, 0.5), Sphere(0, -9000, 0, 8999.3, np.array([0.1, 0.1, 0.1]), np.array([0.5, 0.5, 0.5]), np.array([1, 1, 1]), 100, 0.5)])
# for val in rgb_range: #g
#     objects.append([Sphere(0, 0, -1, 0.8, np.array([0, 0.1, 0]), np.array([0, val, 0]), np.array([1, 1, 1]), 100, 0.5), Sphere(0, -9000, 0, 8999.3, np.array([0.1, 0.1, 0.1]), np.array([0.5, 0.5, 0.5]), np.array([1, 1, 1]), 100, 0.5)])
# for val in rgb_range_back:
#     objects.append([Sphere(0, 0, -1, 0.8, np.array([0, 0.1, 0]), np.array([0, val, 0]), np.array([1, 1, 1]), 100, 0.5), Sphere(0, -9000, 0, 8999.3, np.array([0.1, 0.1, 0.1]), np.array([0.5, 0.5, 0.5]), np.array([1, 1, 1]), 100, 0.5)])
# for val in rgb_range: #b
#     objects.append([Sphere(0, 0, -1, 0.8, np.array([0, 0, 0.1]), np.array([0, 0, val]), np.array([1, 1, 1]), 100, 0.5), Sphere(0, -9000, 0, 8999.3, np.array([0.1, 0.1, 0.1]), np.array([0.5, 0.5, 0.5]), np.array([1, 1, 1]), 100, 0.5)])
# for val in rgb_range_back:
#     objects.append([Sphere(0, 0, -1, 0.8, np.array([0, 0, 0.1]), np.array([0, 0, val]), np.array([1, 1, 1]), 100, 0.5), Sphere(0, -9000, 0, 8999.3, np.array([0.1, 0.1, 0.1]), np.array([0.5, 0.5, 0.5]), np.array([1, 1, 1]), 100, 0.5)])
    
#creating spheres + "plane"
# objects.append(Sphere(0.6, 1, -5, 1, np.array([0.1, 0.1, 0]), np.array([0.6, 0.3, 0]), np.array([1, 1, 1]), 100, 0.5))
# objects.append(Sphere(-0.9, 0.6, -4, 1.5, np.array([0.05, 0.1, 0.1]), np.array([0.1, 0.6, 0.7]), np.array([1, 1, 1]), 100, 0.5))
# objects.append(Sphere(2.1, 3, -10, 4, np.array([0.3, 0, 0]), np.array([0.5, 0, 0]), np.array([1, 1, 1]), 100, 0.5))
# objects.append(Sphere(-2.1, 0, -1.5, 0.4, np.array([0.1, 0, 0.1]), np.array([0.7, 0, 0.8]), np.array([1, 1, 1]), 100, 0.5))
# objects.append(Sphere(0.8, 0.2, -1, 0.18, np.array([0, 0.1, 0.1]), np.array([0, 0.7, 0.6]), np.array([1, 1, 1]), 100, 0.5))
# objects.append(Sphere(0, -9000, 0, 8999.3, np.array([0.1, 0.1, 0.1]), np.array([0.5, 0.5, 0.5]), np.array([1, 1, 1]), 100, 0.5))


#create light source(s)
light = Light(5, 5, 5, np.array([1, 1, 1]), np.array([1, 1, 1]), np.array([1, 1, 1]))
# lights = []
# for y in y_range:
#     light = make_light(5+y, 5, 5+y, np.array([1, 1, 1]), np.array([1, 1, 1]), np.array([1, 1, 1]))
#     lights.append(light)

#reflection depth
reflect_depth = 3

In [5]:
#change first argument to whatever you are animating
def generate_image(objects, image):
    for i, y in enumerate(np.linspace(screen[1], screen[3], h)):
        for j, x in enumerate(np.linspace(screen[0], screen[2], w)):
            origin = camera
            curr_pixel = np.array([x, y, 0]) #current pixel of screen
            ray = norm(curr_pixel - origin) #ray from camera through screen, normalized
            final_values = np.zeros((3)) #what will be filled in pixel at end
            reflection = 1 #reflection coefficient, gets decreased every time reflection happens for this pixel

            #ray geometry source: https://gist.github.com/omaraflak/bfaa3dcc2224c17f50ac4f7524323444#file-medium_ray_tracing_code_7-py
            for k in range(reflect_depth):
                #try to get the nearest object. if none, fill with black space = 0
                nearest_object, min_dist = find_nearest_object(objects, origin, ray)
                if nearest_object is None:
                    break

                closest_ray = origin + min_dist*ray
                surface = norm(closest_ray - nearest_object.get_center())

                shift_intersect = closest_ray + 0.0001*surface
                intersect_from_light = norm(light.get_center() - shift_intersect)

                _, min_dist = find_nearest_object(objects, shift_intersect, intersect_from_light)
                intersect_light_dist = np.linalg.norm(light.get_center() - closest_ray)

                shadow = min_dist < intersect_light_dist
                if shadow:
                    break

                #object/light parameters
                obj_ambient = nearest_object.ambient
                obj_diffuse = nearest_object.diffuse
                obj_specular = nearest_object.specular
                obj_shine = nearest_object.shine
                obj_reflect = nearest_object.reflect
                light_ambient = light.ambient
                light_diffuse = light.diffuse
                light_specular = light.specular

                color = np.zeros((3)) #color to be filled in with optical properties

                #ambient
                color += light_ambient*obj_ambient
                #diffuse
                color += light_diffuse*obj_diffuse*np.dot(intersect_from_light, surface)
                #specular
                camera_intersect = norm(camera - closest_ray)
                final_intersect = norm(intersect_from_light + camera_intersect)
                color += obj_specular * light_specular * np.dot(surface, final_intersect)**(obj_shine/4) #blinn-phong specular exponent
                #reflection
                final_values += reflection*color
                reflection *= obj_reflect
                #shift the origin to the reflected point for the next ray tracing
                origin = shift_intersect
                ray = reflected_ray(ray, surface)


            image[i, j] = np.clip(final_values, 0, 1)
    #plt.imshow(image)
    return image

In [6]:
# Set up animation
metadata = dict(title='Ray tracing Animation', artist='Matplotlib',comment='Moving camera frame.')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)

fig = fig = plt.figure(dpi=200)
filename = "test.mp4"

with writer.saving(fig, filename, dpi=200):
    #initialize image
    image = np.zeros((h, w, 3))
    
#     #Section 1: make one image
#     fig.clear()
#     curr_image = generate_image(camera, image)
#     plt.axis('off')
#     plt.imshow(curr_image)
    #End Section 1
    
    
    #Section 2: animation- un/comment as needed.
    for i in range(len(objects)):
        if i%10 == 0:
            print("Rendering frame", i, "of", len(objects))
        
        curr_object = objects[i]
        curr_image = generate_image(curr_object, image)
        
#         curr_camera = cameras[i]
#         curr_image = generate_image(curr_camera, image)

#         curr_screen = screens[i] #TODO if time

#         curr_light = lights[i]
#         curr_image = generate_image(curr_light, image)
        plt.axis('off')
        plt.imshow(curr_image)
        plt.pause(0.05)
        writer.grab_frame()
        image = np.copy(curr_image)

Rendering frame 0 of 100


KeyboardInterrupt: 